In [1]:
import sys
import os
import glob
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

import wave
import soundfile as sf
import librosa as lb

import dask

from IPython.display import Audio

import os

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense,Dropout,Activation,Flatten
from tensorflow.keras.optimizers import Adam
from sklearn import metrics
import tensorflow.keras as keras

from pathlib import Path

from IPython.display import Audio
from IPython.utils import io
from synthesizer.inference import Synthesizer
from encoder import inference as encoder
from vocoder import inference as vocoder

from tqdm import tqdm
# import encoder

D:\Workspace\Data_Science\Real-Time-Voice-Cloning-master\synthesizer\utils\plot.py:2: UserWarning: matplotlib.pyplot as already been imported, this call will have no effect.
  matplotlib.use("Agg")
D:\Workspace\Data_Science\Real-Time-Voice-Cloning-master\encoder\audio.py:13: UserWarning: Unable to import 'webrtcvad'. This package enables noise removal and is recommended.
  warn("Unable to import 'webrtcvad'. This package enables noise removal and is recommended.")


In [2]:
path1 = "D:\\Workspace\\Data_Science\\archive\\data\\TRAIN"
os.chdir( path1 )

In [3]:
# Directories to loop through

directories = next(os.walk(path1))[1]

new_path = []

for d in directories:
    d_path = path1 + '/' + d
    new_path.append(d_path)

In [4]:
# Save all the directories in a list

all_directories = []

for i,j in enumerate(new_path):
    folder_directories = next(os.walk(new_path[i]))[1]
    
    for d in folder_directories:
        current_directory = new_path[i] + '/' + d
        all_directories.append(current_directory)

In [5]:
# Create a function to have the different audio samples and run the voice-cloner function

def preprocessor(paths):
    
    sample_audios = []
    
    for path in paths:
        audio_files = glob.glob(path + '/*.WAV')
        audio_file, freq = lb.load(audio_files[0])
        freq = np.array(freq)
        
        for i in range(1, len(audio_files)):
            audio, freqs = lb.load(audio_files[i])
            audio_file = np.concatenate((audio_file, audio), axis = None)
            freqs = np.concatenate((freq, freqs), axis = None)
            
        sample_audios.append(audio_file)
        
    return sample_audios

In [6]:
# Create a function to have the different audio samples and run the voice-cloner function

def preprocessor(paths):
    
    sample_audios = []
    
    for path in paths:
        audio_files = glob.glob(path + '/*.WAV')
        audio_file, freq = lb.load(audio_files[0])
        freq = np.array(freq)
        
        for i in range(1, len(audio_files)):
            audio, freqs = lb.load(audio_files[i])
            audio_file = np.concatenate((audio_file, audio), axis = None)
            freqs = np.concatenate((freq, freqs), axis = None)
            
        sample_audios.append(audio_file)
        
    return sample_audios

In [7]:

# Apply the function to all the directories

sample_audios = preprocessor(paths = all_directories)

In [8]:
Audio(data = sample_audios[2], rate = 22050)

In [9]:
# Display a sample audio

Audio(data = sample_audios[0], rate = 22050)

In [10]:
# Import warnings before downloading the data

import warnings

In [14]:
# Filter all the warnings

warnings.filterwarnings(action = 'ignore')

path3 = 'D:\\Workspace\\Data_Science\\cv-corpus-7.0-2021-07-21-en.tar\\cv-corpus-7.0-2021-07-21-en\\cv-corpus-7.0-2021-07-21\\en\\clips'
os.chdir( path3 )

# Download the data from the different paths

def preprocessor_real_data(path, n_clips = 500):
    real_data = []
    freqs = []
    audio_files = glob.glob(path + '/*.mp3')
    
    for i in range(0, n_clips):
        
        if(i%50 == 0):
            print(i)
        
        try:
            audio, freqs = lb.load(audio_files[i])
            real_data.append(audio)
            
        except:
            pass
        
    return real_data

In [15]:
real_clips = preprocessor_real_data(path = path3,n_clips = 500)

0
50
100
150
200
250
300
350
400
450


In [16]:
print(len(real_clips))

500


## Voice Cloning

In [18]:
# Change directory
path3 = 'D:\\Workspace\\Data_Science\\Real-Time-Voice-Cloning-master'
os.chdir( path3 )

In [19]:
os.getcwd()

'D:\\Workspace\\Data_Science\\Real-Time-Voice-Cloning-master'

In [21]:
# Establish the path for the encoder, vocoder and synthesizer

encoder_weights = Path("pretrained/encoder/saved_models/pretrained.pt")
vocoder_weights = Path('pretrained/vocoder/saved_models/pretrained/pretrained.pt')
syn_dir = Path('pretrained/synthesizer/saved_models/logs-pretrained/taco_pretrained')


In [22]:
# Load each of the models

encoder.load_model(encoder_weights)
synthesizer = Synthesizer(syn_dir)
vocoder.load_model(vocoder_weights)

Loaded encoder "pretrained.pt" trained to step 1564501
Found synthesizer "pretrained" trained to step 278000
Building Wave-RNN
Trainable Parameters: 4.481M
Loading model weights at pretrained\vocoder\saved_models\pretrained\pretrained.pt


In [23]:
# Clone with the first half some sentences

def voice_cloning(audios_to_clon, text_to_clon):
    
    audio_cloned = []
    
    for i in range(0, int(len(audios_to_clon)/2)):
        
        audio = audios_to_clon[i]
        
        # Reprocess all of the audios

        reprocessed_wav = encoder.preprocess_wav(audio)

        # Preprocess the audios with the encoder (audio and the frequency)

        preprocessed_wav = encoder.preprocess_wav(audio, 22050)

        # use encoder.embed_utterance
        embed = encoder.embed_utterance(preprocessed_wav)

        with io.capture_output() as captured:
            specs = synthesizer.synthesize_spectrograms([text_to_clon], [embed])
            

        generated_wav = vocoder.infer_waveform(specs[0])

        generated_wav = np.pad(generated_wav, (0,synthesizer.sample_rate), mode = 'constant')
        
        audio_cloned.append(generated_wav)
        
    return audio_cloned

In [24]:
# Clone with the second half other sentence

def voice_cloning_2(audios_to_clon, text_to_clon):
    
    audio_cloned = []
    
    for i in range(int(len(audios_to_clon)/2), len(audios_to_clon)-1):
        
        audio = audios_to_clon[i]
        
        # Reprocess all of the audios

        reprocessed_wav = encoder.preprocess_wav(audio)

        # Preprocess the audios with the encoder (audio and the frequency)

        preprocessed_wav = encoder.preprocess_wav(audio, 22050)

        # use encoder.embed_utterance
        embed = encoder.embed_utterance(preprocessed_wav)

        with io.capture_output() as captured:
            specs = synthesizer.synthesize_spectrograms([text_to_clon], [embed])
            

        generated_wav = vocoder.infer_waveform(specs[0])

        generated_wav = np.pad(generated_wav, (0,synthesizer.sample_rate), mode = 'constant')
        
        audio_cloned.append(generated_wav)
        
    return audio_cloned

In [25]:
# Apply the function for all the files

text = 'Hello, welcome to the course where you can start learning data science while having fun'

cloned_text_1 = voice_cloning(audios_to_clon = sample_audios, text_to_clon = text)

Instructions for updating:
This class is equivalent as tf.keras.layers.LSTMCell, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
Use `tf.keras.layers.Conv1D` instead.
Instructions for updating:
Please use `layer.__call__` method instead.
Instructions for updating:
Use keras.layers.BatchNormalization instead.  In particular, `tf.control_dependencies(tf.GraphKeys.UPDATE_OPS)` should not be used (consult the `tf.keras.layers.batch_normalization` documentation).
Instructions for updating:
Use keras.layers.dropout instead.
Instructions for updating:
Please use `keras.layers.Bidirectional(keras.layers.RNN(cell))`, which is equivalent to this API
Instructions for updating:
Please use `keras.layers.RNN(cell)`, which is equivalent to this API
Instructions for updating:
Please use `layer.add_weight` method instead.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Use tf.wher

In [26]:
# Define text 2

text2 = 'She is planning a trip to the West Coast. She wants to go to California and Los Angeles'

cloned_text_2 = voice_cloning_2(audios_to_clon = sample_audios, text_to_clon = text2)

{| ████████████████ 76000/76800 | Batch Size: 8 | Gen Rate: 3.0kHz | }

In [27]:
# Display a sample

display(Audio(cloned_text_2[4], rate = synthesizer.sample_rate))

In [28]:
# Display a sample

display(Audio(cloned_text_1[4], rate = synthesizer.sample_rate))

## Data Preprocessing

In [29]:

# Calculate the expected samples for future padding

def get_expected_samples(audio):
    num_samples = len(audio)
    return num_samples

In [30]:
# Get the number of total samples

total_samples = []

for i in range(0, len(real_clips)):
    sample = get_expected_samples(audio = real_clips[i])
    total_samples.append(sample)
    
for i in range(0, len(cloned_text_1)):
    sample = get_expected_samples(audio = cloned_text_1[i])
    total_samples.append(sample)
    
for i in range(0, len(cloned_text_2)):
    sample = get_expected_samples(audio = cloned_text_2[i])
    total_samples.append(sample)

In [31]:
print(len(real_clips))

500


In [32]:
print(len(cloned_text_2))

230


In [33]:
# Calculate the expected samples for padding

expected_samples = max(total_samples)

print('Expected samples are: {}'.format(expected_samples))

Expected samples are: 482102


In [34]:
# Pad if necessary (Zero Right pad) to make sure we will have arrays with same dimensions

def apply_padding(audio, num_expected):
    num_missing_samples = num_expected - len(audio)
    zeros = np.zeros(num_missing_samples)
    new_array = np.concatenate((audio, zeros), axis = None)
    return new_array

In [35]:
# Apply the padding for all if necessary

real_clips_padded = []

for i in range(0, len(real_clips)):
    sample = apply_padding(audio = real_clips[i], num_expected = expected_samples)
    real_clips_padded.append(sample)
    
fake_clips_padded1 = []
    
for i in range(0, len(cloned_text_1)):
    sample = apply_padding(audio = cloned_text_1[i], num_expected = expected_samples)
    fake_clips_padded1.append(sample)
    
fake_clips_padded2 = []
    
for i in range(0, len(cloned_text_2)):
    sample = apply_padding(audio = cloned_text_2[i], num_expected = expected_samples)
    fake_clips_padded2.append(sample)

In [36]:
# Define a function to extract the features of each file

def feature_extractor(audio):
    audio_mfccs = lb.feature.mfcc(audio, n_fft=1024 , hop_length = 528, n_mfcc = 20, center = False)
    audio_mfccs = audio_mfccs.T
    
    return audio_mfccs

In [38]:
# Real clips

scaled_real_audios = np.zeros(shape = (len(real_clips_padded), 912, 20))

for i in range(0, len(real_clips_padded)):
    scaled_real_audios[i] = feature_extractor(audio = real_clips_padded[i])
    
    
# Voice cloner first part

scaled_fake_audios1 = np.zeros(shape = (len(fake_clips_padded1), 912,20))

for i in range(0, len(fake_clips_padded1)):
    scaled_fake_audios1[i] = feature_extractor(audio = fake_clips_padded1[i])
    

# Voice cloner second part
scaled_fake_audios2 = np.zeros(shape = (len(fake_clips_padded2), 912,20))
    
for i in range(0, len(fake_clips_padded2)):
    scaled_fake_audios2[i] = feature_extractor(audio = fake_clips_padded2[i])

In [39]:

# Define the classes for both scenarios
# For this specific scenario, 0 would be fake voices and 1 would be a real voice

fake_class_1 = np.array([0 for i in range(0,len(scaled_fake_audios1))])

fake_class_2 = np.array([0 for i in range(0, len(scaled_fake_audios2))])

real_class = np.array([1 for i in range(0,len(scaled_real_audios))])

In [40]:

# Concatenate the three arrays for the X

X = np.concatenate((scaled_real_audios, scaled_fake_audios1, scaled_fake_audios2), axis = 0)

y = np.concatenate((real_class, fake_class_1, fake_class_2), axis = 0)

In [41]:
# Divide into train and test 

from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.25, random_state = 32)

In [44]:

# Add new axis

X_train = X_train[..., np.newaxis]

X_test = X_test[..., np.newaxis]

## Modeling

In [45]:
# Define a model for the Convulsional neural network

def build_model(input_shape):
    """Generates CNN model
    :param input_shape (tuple): Shape of input set
    :return model: CNN model
    """

    # build network topology
    model = keras.Sequential()

    # 1st conv layer
    model.add(keras.layers.Conv2D(32, (3, 3), activation='relu', input_shape=input_shape))
    model.add(keras.layers.MaxPooling2D((3, 3), strides=(2, 2), padding='same'))
    model.add(keras.layers.BatchNormalization())

    # 2nd conv layer
    model.add(keras.layers.Conv2D(32, (3, 3), activation='relu'))
    model.add(keras.layers.MaxPooling2D((3, 3), strides=(2, 2), padding='same'))
    model.add(keras.layers.BatchNormalization())

    # 3rd conv layer
    model.add(keras.layers.Conv2D(32, (2, 2), activation='relu'))
    model.add(keras.layers.MaxPooling2D((2, 2), strides=(2, 2), padding='same'))
    model.add(keras.layers.BatchNormalization())

    # flatten output and feed it into dense layer
    model.add(keras.layers.Flatten())
    model.add(keras.layers.Dense(64, activation='relu'))
    model.add(keras.layers.Dropout(0.3))

    # output layer
    model.add(keras.layers.Dense(10, activation='softmax'))

    return model

In [47]:
# Create the model

model = build_model(input_shape = (912, 20, 1))

In [48]:
# compile model
optimizer = keras.optimizers.Adam(learning_rate=0.0001)

model.compile(optimizer=optimizer, loss='sparse_categorical_crossentropy',metrics=['accuracy'])

In [49]:
# Fit the model

model.fit(X_train, y_train, validation_data=(X_test, y_test), batch_size=32, epochs=10)

Train on 720 samples, validate on 241 samples
Epoch 1/10
720/720 [==============================] - ETA: 11s - loss: 2.8560 - acc: 0.06 - ETA: 8s - loss: 2.5782 - acc: 0.1406 - ETA: 7s - loss: 2.3589 - acc: 0.177 - ETA: 6s - loss: 2.0731 - acc: 0.296 - ETA: 6s - loss: 1.8550 - acc: 0.375 - ETA: 5s - loss: 1.6687 - acc: 0.437 - ETA: 5s - loss: 1.5431 - acc: 0.473 - ETA: 4s - loss: 1.4491 - acc: 0.496 - ETA: 4s - loss: 1.3572 - acc: 0.524 - ETA: 4s - loss: 1.2684 - acc: 0.559 - ETA: 3s - loss: 1.2011 - acc: 0.573 - ETA: 3s - loss: 1.1431 - acc: 0.591 - ETA: 3s - loss: 1.0952 - acc: 0.605 - ETA: 2s - loss: 1.0628 - acc: 0.611 - ETA: 2s - loss: 1.0139 - acc: 0.629 - ETA: 2s - loss: 0.9780 - acc: 0.644 - ETA: 1s - loss: 0.9411 - acc: 0.654 - ETA: 1s - loss: 0.9011 - acc: 0.666 - ETA: 1s - loss: 0.8613 - acc: 0.682 - ETA: 0s - loss: 0.8264 - acc: 0.695 - ETA: 0s - loss: 0.7998 - acc: 0.702 - ETA: 0s - loss: 0.7768 - acc: 0.708 - 7s 10ms/sample - loss: 0.7632 - acc: 0.7139 - val_loss: 1.4821 

720/720 [==============================] - ETA: 7s - loss: 0.0028 - acc: 1.000 - ETA: 6s - loss: 0.0026 - acc: 1.000 - ETA: 6s - loss: 0.0036 - acc: 1.000 - ETA: 6s - loss: 0.0117 - acc: 1.000 - ETA: 5s - loss: 0.0097 - acc: 1.000 - ETA: 5s - loss: 0.0087 - acc: 1.000 - ETA: 5s - loss: 0.0089 - acc: 1.000 - ETA: 4s - loss: 0.0084 - acc: 1.000 - ETA: 4s - loss: 0.0083 - acc: 1.000 - ETA: 4s - loss: 0.0076 - acc: 1.000 - ETA: 3s - loss: 0.0077 - acc: 1.000 - ETA: 3s - loss: 0.0075 - acc: 1.000 - ETA: 3s - loss: 0.0078 - acc: 1.000 - ETA: 2s - loss: 0.0075 - acc: 1.000 - ETA: 2s - loss: 0.0073 - acc: 1.000 - ETA: 2s - loss: 0.0071 - acc: 1.000 - ETA: 1s - loss: 0.0071 - acc: 1.000 - ETA: 1s - loss: 0.0074 - acc: 1.000 - ETA: 1s - loss: 0.0073 - acc: 1.000 - ETA: 0s - loss: 0.0073 - acc: 1.000 - ETA: 0s - loss: 0.0074 - acc: 1.000 - ETA: 0s - loss: 0.0073 - acc: 1.000 - 8s 12ms/sample - loss: 0.0072 - acc: 1.0000 - val_loss: 0.0460 - val_acc: 0.9917
Epoch 10/10
720/720 [===================

## Model Evaluation

In [50]:
# Evaluate model on test set
test_loss, test_acc = model.evaluate(X_test, y_test, verbose=2)
print('\nTest accuracy:', test_acc)

241/241 - 1s - loss: 0.0349 - acc: 0.9959

Test accuracy: 0.9958506


In [51]:
# Empty array to save predictions

predictions = np.zeros(shape = len(X_test))

# Calculate the predictions

for i in range(0, len(X_test)):
    sample = X_test[i]
    sample = sample[np.newaxis, ...]
    prediction = model.predict(sample)
    predictions[i] = np.argmax(prediction, axis = 1)

In [52]:
# Confusion matrix

from sklearn.metrics import (confusion_matrix,classification_report)

# Evaluate the model using a confusion matrix

cm = confusion_matrix(y_test, predictions)
# cmd = ConfusionMatrixDisplay(cm, display_labels=['fake','real'])
# cmd.plot()

# plt.show()

In [53]:
import seaborn as sns
print(classification_report(y_test, predictions))

              precision    recall  f1-score   support

           0       1.00      0.99      1.00       114
           1       0.99      1.00      1.00       127

    accuracy                           1.00       241
   macro avg       1.00      1.00      1.00       241
weighted avg       1.00      1.00      1.00       241



In [ ]:
}